<a href="https://colab.research.google.com/github/sibiraja/cs2241project/blob/main/New_CS2241.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Install Packages and Set Up

In [ ]:
# Install necessary packages
!pip install torch transformers datasets

# Clone the Arithmetic Coding repo
!git clone https://github.com/nayuki/Reference-arithmetic-coding.git

# Imports
import os
import sys
import io
import math
import numpy as np
import torch
import torch.nn.functional as F
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForCausalLM

# Add the arithmetic coding repo to path
sys.path.append("Reference-arithmetic-coding/python")
from arithmeticcoding import ArithmeticEncoder, SimpleFrequencyTable, BitOutputStream

print("GPU available:", torch.cuda.is_available())

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 112.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 94.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 59.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 59.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 41.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

#1. Helper Functions

In [ ]:
# Create a frequency table from probabilities using top-k tokens
def create_frequency_table_topk(probs_np, total=4096, k=500):
    topk_indices = np.argsort(-probs_np)[:k]
    topk_probs = probs_np[topk_indices]
    topk_probs = topk_probs / topk_probs.sum()  # Normalize
    freqs = np.floor(topk_probs * total).astype(int)
    freqs = np.maximum(freqs, 1)

    current_total = freqs.sum()
    diff = total - current_total
    if diff > 0:
        indices = np.argsort(-topk_probs)
        for idx in indices:
            if diff <= 0:
                break
            freqs[idx] += 1
            diff -= 1
    elif diff < 0:
        indices = np.argsort(topk_probs)
        for idx in indices:
            if diff >= 0:
                break
            if freqs[idx] > 1:
                freqs[idx] -= 1
                diff += 1

    return topk_indices, freqs.tolist()

# Arithmetic encode a token
def arithmetic_encode_token_topk(probs, token_id, total=4096, k=500):
    probs_np = probs.cpu().numpy()
    topk_indices, freqs = create_frequency_table_topk(probs_np, total=total, k=k)

    if token_id not in topk_indices:
        raise ValueError("Token not in top-k set for encoding.")

    mapped_token_id = int(np.where(topk_indices == token_id)[0][0])

    freq_table = SimpleFrequencyTable(freqs)
    output = io.BytesIO()
    bitout = BitOutputStream(output)
    encoder = ArithmeticEncoder(32, bitout)
    encoder.write(freq_table, mapped_token_id)
    encoder.finish()
    encoded_bytes = output.getvalue()
    return encoded_bytes


In [ ]:
# GZIP compression
import gzip

def compress_gzip(text):
    compressed = gzip.compress(text.encode('utf-8'))
    return compressed

In [ ]:
# LZW compression
def lzw_compress(uncompressed):
    uncompressed_bytes = uncompressed.encode('utf-8')
    dict_size = 256
    dictionary = {bytes([i]): i for i in range(dict_size)}
    w = b""
    result = []
    for b in uncompressed_bytes:
        c = bytes([b])
        wc = w + c
        if wc in dictionary:
            w = wc
        else:
            result.append(dictionary[w])
            dictionary[wc] = dict_size
            dict_size += 1
            w = c
    if w:
        result.append(dictionary[w])
    return result

def lzw_compression_ratio(text):
    original_size = len(text.encode('utf-8'))
    compressed_codes = lzw_compress(text)
    if not compressed_codes:
        return 0, 0
    max_code = max(compressed_codes)
    bits_per_code = math.ceil(math.log2(max_code + 1))
    compressed_size_bits = len(compressed_codes) * bits_per_code
    compressed_size_bytes = compressed_size_bits / 8
    ratio = compressed_size_bytes / original_size
    return ratio, len(compressed_codes)


# 2. Load Datasets


In [ ]:
# Load general English dataset (TREC)
trec_dataset = load_dataset("trec")
trec_texts = [item["text"] for item in trec_dataset["train"] if len(item["text"].strip()) > 0]

# print(f"TREC sample:\n{trec_texts[0]}")

for i in range(len(trec_texts)):
    print(f"TREC sample {i}: {trec_texts[i]}")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

trec.py:   0%|          | 0.00/5.09k [00:00<?, ?B/s]

The repository for trec contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/trec.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N] y


Generating train split:   0%|          | 0/5452 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/500 [00:00<?, ? examples/s]

TREC sample 0: How did serfdom develop in and then leave Russia ?
TREC sample 1: What films featured the character Popeye Doyle ?
TREC sample 2: How can I find a list of celebrities ' real names ?
TREC sample 3: What fowl grabs the spotlight after the Chinese Year of the Monkey ?
TREC sample 4: What is the full form of .com ?
TREC sample 5: What contemptible scoundrel stole the cork from my lunch ?
TREC sample 6: What team did baseball 's St. Louis Browns become ?
TREC sample 7: What is the oldest profession ?
TREC sample 8: What are liver enzymes ?
TREC sample 9: Name the scar-faced bounty hunter of The Old West .
TREC sample 10: When was Ozzy Osbourne born ?
TREC sample 11: Why do heavier objects travel downhill faster ?
TREC sample 12: Who was The Pride of the Yankees ?
TREC sample 13: Who killed Gandhi ?
TREC sample 14: What is considered the costliest disaster the insurance industry has ever faced ?
TREC sample 15: What sprawling U.S. state boasts the most airports ?
TREC sample 1

In [ ]:
# Load medical dataset (MedQuAD)
medquad_dataset = load_dataset("keivalya/MedQuad-MedicalQnADataset")
print(medquad_dataset)
medquad_texts = [item["Question"] for item in medquad_dataset["train"] if len(item["Question"].strip()) > 0]

# print(f"MedQuAD sample:\n{medquad_texts[0]}")

for i in range(len(medquad_texts)):
    print(f"MedQuAD sample {i}: {medquad_texts[i]}")

README.md:   0%|          | 0.00/233 [00:00<?, ?B/s]

medDataset_processed.csv:   0%|          | 0.00/22.5M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/16407 [00:00<?, ? examples/s]

Streaming output truncated to the last 5000 lines.
MedQuAD sample 11407: What are the symptoms of Otodental dysplasia ?
MedQuAD sample 11408: What is (are) Pseudoxanthoma elasticum ?
MedQuAD sample 11409: What are the symptoms of Pseudoxanthoma elasticum ?
MedQuAD sample 11410: How to diagnose Pseudoxanthoma elasticum ?
MedQuAD sample 11411: What are the treatments for Pseudoxanthoma elasticum ?
MedQuAD sample 11412: What is (are) Myotonic dystrophy type 1 ?
MedQuAD sample 11413: What are the symptoms of Myotonic dystrophy type 1 ?
MedQuAD sample 11414: Is Myotonic dystrophy type 1 inherited ?
MedQuAD sample 11415: What are the treatments for Myotonic dystrophy type 1 ?
MedQuAD sample 11416: What is (are) Chromosome 1p deletion ?
MedQuAD sample 11417: What is (are) Dermal eccrine cylindroma ?
MedQuAD sample 11418: What are the symptoms of Mannosidosis, beta A, lysosomal ?
MedQuAD sample 11419: What is (are) Geographic tongue ?
MedQuAD sample 11420: What are the symptoms of Geographic t

In [ ]:
casehold_dataset = load_dataset("casehold/casehold", "all")

casehold_texts = []

for item in casehold_dataset["train"]:
    label = item["label"]
    correct_holding = item[f"holding_{label}"]

    if len(correct_holding) < 200:  # Short, clean legal sentences
        casehold_texts.append(correct_holding)

print(f"Total filtered CaseHold samples: {len(casehold_texts)}")
# print(f"Sample:\n{casehold_texts[0]}")

for i in range(len(casehold_texts)):
    print(f"CaseHold sample {i}: {casehold_texts[i]}")

casehold.py:   0%|          | 0.00/8.68k [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/46.2M [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/5.79M [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/5.81M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/42509 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/5314 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5314 [00:00<?, ? examples/s]

Total filtered CaseHold samples: 30612
CaseHold sample 0: holding that possession of a pipe bomb is a crime of violence for purposes of 18 usc  3142f1
CaseHold sample 1: holding that included among trade secrets employee may not appropriate from employer is certain information such as lists of customers
CaseHold sample 2: holding that a specific statutory provision prevails over a more general one
CaseHold sample 3: holding that united states v booker 543 us 220 125 sct 738 160 led2d 621 2005 does not provide a basis for a sentence reduction under 18 usc  3582c
CaseHold sample 4: holding that the existence of genuine issues of material facts render not appealable a pretrial denial of summary judgment on the issue of qualified immunity
CaseHold sample 5: holding commercial fishermen may recover for pollution resulting from defendants oil spill
CaseHold sample 6: holding that the proceeds of a liability insurance policy were not property of the estate
CaseHold sample 7: recognizing that 

#3. Load Pretrained LLMs

In [ ]:
# Load GPT-2 model and tokenizer
gpt2_tokenizer = AutoTokenizer.from_pretrained("gpt2")
gpt2_model = AutoModelForCausalLM.from_pretrained("gpt2")
gpt2_model.eval()
gpt2_model.to('cuda' if torch.cuda.is_available() else 'cpu')

print("Loaded GPT-2 model successfully.")

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

Loaded GPT-2 model successfully.


#4. Encoding Pipeline

In [ ]:
# Encode text and calculate total bits used
def encode_text_topk(text, model, tokenizer, total=4096, k=500):
    tokens = tokenizer(text, return_tensors="pt")
    input_ids = tokens.input_ids.to(model.device)
    total_bits = 0

    bos_id = tokenizer.bos_token_id if tokenizer.bos_token_id is not None else tokenizer.eos_token_id
    bos_context = torch.tensor([[bos_id]]).to(model.device)

    for i in range(input_ids.shape[1]):
        context = bos_context if i == 0 else input_ids[:, :i]
        with torch.no_grad():
            outputs = model(context)
        logits = outputs.logits[0, -1, :]
        probs = F.softmax(logits, dim=-1)
        token_id = input_ids[0, i].item()

        try:
            encoded_bytes = arithmetic_encode_token_topk(probs, token_id, total=total, k=k)
            total_bits += len(encoded_bytes) * 8
        except ValueError:
            # Token not in top-k, approximate fallback cost
            total_bits += math.log2(total)

    return total_bits, input_ids.shape[1]


#5. Run Experiments

In [ ]:
from tqdm import tqdm

# Run compression experiments on a list of texts (with progress bar and prints)
def run_experiments(texts, model, tokenizer, dataset_name="Dataset"):
    results = []

    print(f"\nStarting experiments for {dataset_name}...")
    for idx, text in enumerate(tqdm(texts, desc=f"Encoding {dataset_name} texts")):
        if not text.strip():
            continue

        original_size = len(text.encode('utf-8'))

        # LLM arithmetic encoding
        bits_used, n_tokens = encode_text_topk(text, model, tokenizer)
        bpt = bits_used / n_tokens if n_tokens > 0 else 0

        # gzip compression
        gzip_size = len(compress_gzip(text))

        # lzw compression
        lzw_ratio, _ = lzw_compression_ratio(text)
        lzw_size = original_size * lzw_ratio

        results.append({
            "original_size_bytes": original_size,
            "gzip_size_bytes": gzip_size,
            "lzw_size_bytes": lzw_size,
            "llm_bits_total": bits_used,
            "llm_bits_per_token": bpt
        })

        if (idx + 1) % 10 == 0:
            print(f"Processed {idx+1}/{len(texts)} texts for {dataset_name}...")

    print(f"Finished experiments for {dataset_name}!")
    return results


#6. Run initial baseline encoding experiments

In [ ]:
# Run for TREC
trec_results = run_experiments(trec_texts, gpt2_model, gpt2_tokenizer, dataset_name="TREC")

# Run for MedQuAD
medquad_results = run_experiments(medquad_texts, gpt2_model, gpt2_tokenizer, dataset_name="MedQuAD")

# Run for CaseHold
casehold_results = run_experiments(casehold_texts, gpt2_model, gpt2_tokenizer, dataset_name="CaseHold")



Starting experiments for TREC...


Encoding TREC texts:   0%|          | 11/5452 [00:01<10:35,  8.57it/s]

Processed 10/5452 texts for TREC...


Encoding TREC texts:   0%|          | 21/5452 [00:03<10:20,  8.75it/s]

Processed 20/5452 texts for TREC...


...

Processed 4050/30612 texts for CaseHold...


Encoding CaseHold texts:  13%|█▎        | 4060/30612 [19:23<1:43:16,  4.29it/s]

Processed 4060/30612 texts for CaseHold...


Encoding CaseHold texts:  13%|█▎        | 4067/30612 [19:25<2:06:44,  3.49it/s]


KeyboardInterrupt: 

#7. Summarize initial results

In [ ]:
# Summarize Results
import pandas as pd

def summarize_results(results, name):
    df = pd.DataFrame(results)
    print(f"\n=== {name} Dataset Results ===")
    display(df.describe())

summarize_results(trec_results, "TREC")
summarize_results(medquad_results, "MedQuAD")
# summarize_results(casehold_results, "CaseHold")



=== TREC Dataset Results ===


original_size_bytes  gzip_size_bytes  lzw_size_bytes  llm_bits_total  \
count          5452.000000      5452.000000     5452.000000     5452.000000   
mean             50.632062        67.119222       50.448092       45.423331   
std              20.743208        16.499787       19.287510       20.399941   
min              13.000000        33.000000       11.375000        0.000000   
25%              36.000000        55.000000       37.125000       32.000000   
50%              48.000000        66.000000       48.375000       40.000000   
75%              61.000000        77.000000       60.750000       56.000000   
max             196.000000       155.000000      164.250000      192.000000   

       llm_bits_per_token  
count         5452.000000  
mean             4.155984  
std              1.508103  
min              0.000000  
25%              3.076923  
50%              4.000000  
75%              5.142857  
max             11.000000


=== MedQuAD Dataset Results ===


original_size_bytes  gzip_size_bytes  lzw_size_bytes  llm_bits_total  \
count         16407.000000     16407.000000    16407.000000    16407.000000   
mean             50.684952        67.827513       51.158339       48.875480   
std              16.926465        13.449138       16.027120       17.097808   
min              16.000000        36.000000       14.000000        8.000000   
25%              38.000000        58.000000       40.500000       36.000000   
50%              48.000000        67.000000       49.500000       48.000000   
75%              61.000000        77.000000       60.750000       60.000000   
max             191.000000       158.000000      166.500000      156.000000   

       llm_bits_per_token  
count        16407.000000  
mean             4.078711  
std              1.500853  
min              0.400000  
25%              3.076923  
50%              4.000000  
75%              4.800000  
max             11.428571

In [ ]:
# Run for CaseHold
casehold_results = run_experiments(casehold_texts, gpt2_model, gpt2_tokenizer, dataset_name="CaseHold")

# Summarize Results
import pandas as pd

def summarize_results(results, name):
    df = pd.DataFrame(results)
    print(f"\n=== {name} Dataset Results ===")
    display(df.describe())
summarize_results(casehold_results, "CaseHold")


Starting experiments for CaseHold...


Encoding CaseHold texts:   0%|          | 10/30612 [00:03<2:18:01,  3.70it/s]

Processed 10/30612 texts for CaseHold...


Encoding CaseHold texts:   0%|          | 20/30612 [00:06<2:23:25,  3.55it/s]

Processed 20/30612 texts for CaseHold...


...

Encoding CaseHold texts: 100%|█████████▉| 30610/30612 [2:20:07<00:00,  3.94it/s]

Processed 30610/30612 texts for CaseHold...


Encoding CaseHold texts: 100%|██████████| 30612/30612 [2:20:08<00:00,  3.64it/s]

Finished experiments for CaseHold!

=== CaseHold Dataset Results ===


original_size_bytes  gzip_size_bytes  lzw_size_bytes  llm_bits_total  \
count         30612.000000     30612.000000    30612.000000    30612.000000   
mean            129.843558       109.467006      113.725002       86.782308   
std              38.623308        20.343574       28.676497       32.082202   
min              12.000000        32.000000       10.500000       12.000000   
25%             101.000000        94.000000       92.250000       64.000000   
50%             131.000000       111.000000      114.750000       84.000000   
75%             161.000000       126.000000      136.125000      104.000000   
max             199.000000       160.000000      181.125000      292.000000   

       llm_bits_per_token  
count        30612.000000  
mean             4.060649  
std              1.349260  
min              0.400000  
25%              3.111111  
50%              4.000000  
75%              4.857143  
max             12.000000